In [1]:
from kafka import KafkaConsumer
from json import loads
import json
from time import sleep
import pandas as pd
import influxdb_client
from influxdb_client.client.write_api import SYNCHRONOUS

In [2]:
token = "LuDJ6F7gMj8KqZyms0Q3krl0HKsHPYNvPO6k6dEl2lvzSSYyxyVy951S2hg-loMep5v71fZidBVWb2MqH1qdkA=="
org = "mema_org"
bucket = "mema_bucket"
url = "http://localhost:8086"

In [5]:
with influxdb_client.InfluxDBClient(url=url, token=token, org=org) as client:
            write_api = client.write_api(write_options=SYNCHRONOUS)
            p = influxdb_client.Point("MaoTest").field('accuracy', 0)
            write_api.write(bucket, org, p)

client.close()

In [6]:
class EDDM:
    def __init__(self):
        self.min_error = float('inf')
        self.min_std_dev = float('inf')
        self.last_error_distance = 0
        self.total_error_distance = 0
        self.error_count = 0
        self.last_error_index = -1
        self.current_index = 0

    def add_element(self, is_error):
        self.current_index += 1
        if is_error:
            if self.last_error_index != -1:
                distance = self.current_index - self.last_error_index
                self.total_error_distance += distance
                self.error_count += 1
                mean_distance = self.total_error_distance / self.error_count
                std_dev = ((distance - mean_distance) ** 2) ** 0.5

                if mean_distance > self.min_error:
                    self.min_error = mean_distance

                if std_dev > self.min_std_dev:
                    self.min_std_dev = std_dev

            self.last_error_index = self.current_index

            # Early Drift Detection
            if self.error_count > 30 and mean_distance + 2 * std_dev < self.min_error + 2 * self.min_std_dev:
                return True

        return False


In [7]:
import joblib

# Load the model from the file
model = joblib.load('../albert/model/random_forest_model.joblib')


In [8]:
def split_df(df):
    label = df.pop('attack')
    return df, label

In [11]:
class HaiConsumer:
    def __init__(self, topic, bootstrap_servers):
        self.topic = topic
        self.bootstrap_servers = bootstrap_servers
        self.consumer = KafkaConsumer(
            self.topic,
            bootstrap_servers=self.bootstrap_servers,
            auto_offset_reset='earliest',
            enable_auto_commit=True,
            value_deserializer=lambda x: loads(x.decode('utf-8')))

    def consume(self):
        # Initialize ADWIN detector
        eddm = EDDM()

        counter = 0
        # Perform change detection on the test set
        global change_points
        global accuracies
        global whole_df
        global whole_labels
        change_points = []
        accuracies = []
        whole_df = pd.DataFrame()
        whole_labels = pd.Series()
        # write to file
        with influxdb_client.InfluxDBClient(url=url, token=token, org=org) as client:
            write_api = client.write_api(write_options=SYNCHRONOUS)
            for i, message in enumerate(self.consumer):
                
                message = message.value
                print(message)
                # selected_columns = {key: value for key, value in message.items() if key in columns_to_scale_and_monitor}
                df = pd.DataFrame([message])
                x_i, y_i = split_df(df)
                x_i = x_i.iloc[0:1]
                
                whole_df =pd.concat([whole_df,x_i], ignore_index=True)
                whole_labels = pd.concat([whole_labels,y_i], ignore_index=True)

                # Predict using the RandomForest model
                pred = model.predict(x_i)

                 # Check for a change point using EDDM
                is_error = pred != int(y_i)
                if eddm.add_element(is_error):
                    change_points.append(i)
                # Calculate accuracy at each step
                accuracy = model.score(whole_df.iloc[:i + 1], whole_labels.iloc[:i + 1])
                accuracies.append(accuracy)

                if accuracy >= 0.5:
                    accuracy = 1
                else:
                    accuracy = 0
                
                p = influxdb_client.Point("HAI_ChangeDetection_EDDM").field('current_state', int(accuracy))
                write_api.write(bucket, org, p)

                
                p = influxdb_client.Point("HAI_ChangeDetection_EDDM").field('change_detected', int(y_i))
                write_api.write(bucket, org, p)
                
            client.close()

In [12]:
topic = 'hai-preprocessed-mao-3'
bootstrap_servers = ['localhost:9092']
consumer = HaiConsumer(topic, bootstrap_servers)
consumer.consume()

C:\Users\irenm\AppData\Local\Temp\ipykernel_14248\1480420547.py:25: FutureWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  whole_labels = pd.Series()


{'P1_B2004': 0.0982, 'P1_B2016': 1.5937, 'P1_B3004': 461.9883, 'P1_B3005': 1099.7363, 'P1_B4002': 32.0, 'P1_B4005': 67.5559, 'P1_B400B': 1989.2568, 'P1_B4022': 36.2389, 'P1_FCV01D': 29.2474, 'P1_FCV01Z': 25.7507, 'P1_FCV02D': 0.0, 'P1_FCV02Z': -1.8295, 'P1_FCV03D': 52.6802, 'P1_FCV03Z': 53.8345, 'P1_FT01': 179.1382, 'P1_FT01Z': 845.2607, 'P1_FT02': 959.6253, 'P1_FT02Z': 1929.1067, 'P1_FT03': 302.9251, 'P1_FT03Z': 1100.0421, 'P1_LCV01D': 14.21, 'P1_LCV01Z': 13.9328, 'P1_LIT01': 462.3629, 'P1_PCV01D': 52.2074, 'P1_PCV01Z': 52.095, 'P1_PCV02D': 12.0, 'P1_PCV02Z': 11.6364, 'P1_PIT01': 1.3795, 'P1_PIT02': 1.7267, 'P1_TIT01': 35.2844, 'P1_TIT02': 35.6506, 'P2_24Vdc': 28.0212, 'P2_Auto': 1.0, 'P2_Emgy': 0.0, 'P2_On': 1.0, 'P2_SD01': 0.0, 'P2_SIT01': 792.0, 'P2_TripEx': 0.0, 'P2_VT01e': 11.8338, 'P2_VXT02': -3.7696, 'P2_VXT03': -1.7244, 'P2_VYT02': 0.0098, 'P2_VYT03': 1.3074, 'P3_LCP01D': 904.0, 'P3_LCV01D': 16384.0, 'P3_LH': 70.0, 'P3_LL': 10.0, 'P3_LT01': 47.7141, 'P4_HT_FD': 0.0005, 'P4_HT_